# Exploratory Analysis

In [1]:
from pathlib import Path
import pandas as pd

df = pd.read_csv(Path("cleaned") / "KMB.csv")
df["period_end"] = pd.to_datetime(df["period_end"])
df["filing_date"] = pd.to_datetime(df["filing_date"])
print(df.shape)
df.head(3)

(448, 605)


period_end filing_date    form  AccountsPayableCurrent  \
0 2006-12-31  2010-02-24    10-K                     NaN   
1 2007-12-31  2009-08-07    10-Q                     NaN   
2 2007-12-31  2009-11-06  10-Q/A                     NaN   

   AccountsPayableTradeCurrent  AccountsReceivableNetCurrent  \
0                          NaN                           NaN   
1                          NaN                           NaN   
2                          NaN                           NaN   

   AccruedAdvertisingCurrent  AccruedIncomeTaxesCurrent  \
0                        NaN                        NaN   
1                        NaN                        NaN   
2                        NaN                        NaN   

   AccruedIncomeTaxesNoncurrent  AccruedLiabilitiesCurrent  ...  \
0                           NaN                        NaN  ...   
1                           NaN                        NaN  ...   
2                           NaN                        NaN  ...   

   UnrecordedUnconditionalPurchaseObligationDueAfterFiveYears  \
0                                                NaN            
1                                                NaN            
2                                                NaN            

   ValuationAllowanceDeferredTaxAssetChangeInAmount  \
0                                               NaN   
1                                               NaN   
2                                               NaN   

   ValuationAllowancesAndReservesBalance  \
0                                    NaN   
1                                    NaN   
2                                    NaN   

   ValuationAllowancesAndReservesChargedToCostAndExpense  \
0                                                NaN       
1                                                NaN       
2                                                NaN       

   ValuationAllowancesAndReservesDeductions  \
0                                       NaN   
1                                       NaN   
2                                       NaN   

   ValuationAllowancesAndReservesPeriodIncreaseDecrease  VariableLeaseCost  \
0                                                NaN                   NaN   
1                                                NaN                   NaN   
2                                                NaN                   NaN   

   WeightedAverageNumberOfDilutedSharesOutstanding  \
0                                              NaN   
1                                              NaN   
2                                              NaN   

   WeightedAverageNumberOfSharesIssuedBasic  \
0                                       NaN   
1                                       NaN   
2                                       NaN   

   WeightedAverageNumberOfSharesOutstandingBasic  
0                                            NaN  
1                                            NaN  
2                                            NaN  

[3 rows x 605 columns]

In [2]:
df.dtypes[df.dtypes != float]

period_end     datetime64[ns]
filing_date    datetime64[ns]
form                   object
dtype: object

# Plotting

In [3]:
import matplotlib.pyplot as plt

cols = df.columns
n_cols = 3
n_rows = (len(cols) + n_cols - 1) // n_cols

fig, axes = plt.subplots(n_rows, n_cols, figsize=(15, n_rows * 3), sharex=True)
axes = axes.flatten() # Makes the 2D grid easy to iterate over

print("Creating plots...")
for i, col in enumerate(cols):
    axes[i].scatter(df["period_end"], df[col], color='tab:blue')
    axes[i].set_title(f"{col} ({i}) - {df[col].notna().sum()} data points")
    if i % 100 == 0:
        print(f"Iteration {i}")

# Hide any unused subplots
print("Hiding subplots...")
for j in range(i + 1, len(axes)):
    axes[j].axis('off')
    if j % 100 == 0:
        print(f"Iteration {j}")

print("Plotting...")
plt.tight_layout()

Creating plots...
Iteration 0
Iteration 100
Iteration 200
Iteration 300
Iteration 400
Iteration 500
Iteration 600
Hiding subplots...
Plotting...


Looking for features that can be backtested and are currently available

In [4]:
# not including periodic trends that don't span into present day (i.e. missing data)
possibly_periodic = [
	3, 5, 6, 9, 10, 11, 15, 16, 
	20, 21, 23, 24, 26, 27, 28,
	29, 30, 35, 41, 42, 43, 44, 45,
	46, 51, 52, 53, 54, 55, 56,
	57, 58, 59, 60, 61, 62, 
	63, 64, 65, 66, 67, 71,
	72, 73, 74, 75, 76, 77,
	79, 82, 85, 87, 89, 90,
	93, 95, 97, 98, 99, 101,
	102, 103, 110, 111, 127,
	128, 129, 130, 142, 143,
	146, 153, 157, 158, 159,
	160, 180, 181, 182, 183, 185, 
	186, 187, 188, 189, 194, 
	195, 196, 198, 203, 205,
	206, 217, 236, 238, 239, 
	242, 243, 244, 245, 246,
	247, 258, 262, 263, 264,
	268, 269, 273, 274, 276,
	277, 278, 279, 280, 281,
	282, 283, 284, 287, 288,
	289, 302, 304, 305, 307,
	308, 309, 310, 311, 314,
	318, 319, 320, 322, 323,
	324, 325, 326, 327, 328,
	329, 332, 334, 335, 336, 
	338, 339, 340, 341, 343,
	344, 345, 357, 358, 359,
	361, 362, 363, 364, 365,
	377, 378, 381, 383, 385,
	387, 388, 401, 402, 405, 
	407, 408, 416, 417, 418,
	419, 421, 429, 437, 441,
	442, 444, 445, 451, 455, 
	457, 459, 461, 462, 463, 
	464, 465, 466, 467, 468, 
	469, 472, 474, 475, 477, 
	478, 482, 487, 489, 492,
	494, 496, 497, 499, 500,
	501, 505, 507, 514, 516,
	517, 521, 523, 524, 526,
	528, 529, 530, 554, 558,
	559, 560, 562, 567, 574,
	575, 577, 578, 579, 580,
	581, 582, 583, 585, 586,
	589, 590, 591, 592, 593,
	595, 601, 602, 603, 604,
]

full_feats = [0,1,2] # keep period end, filing date and form type
full_feats.extend(possibly_periodic)

len(full_feats)

254

In [5]:
df = df.iloc[:,full_feats]
print(df.shape)
df.head(3)

(448, 254)


period_end filing_date    form  AccountsPayableCurrent  \
0 2006-12-31  2010-02-24    10-K                     NaN   
1 2007-12-31  2009-08-07    10-Q                     NaN   
2 2007-12-31  2009-11-06  10-Q/A                     NaN   

   AccountsReceivableNetCurrent  AccruedAdvertisingCurrent  \
0                           NaN                        NaN   
1                           NaN                        NaN   
2                           NaN                        NaN   

   AccruedLiabilitiesCurrent  AccruedSalariesCurrent  \
0                        NaN                     NaN   
1                        NaN                     NaN   
2                        NaN                     NaN   

   AccumulatedDepreciationDepletionAndAmortizationPropertyPlantAndEquipment  \
0                                                NaN                          
1                                                NaN                          
2                                                NaN                          

   AccumulatedOtherComprehensiveIncomeLossNetOfTax  ...  \
0                                              NaN  ...   
1                                              NaN  ...   
2                                              NaN  ...   

   UnrecordedUnconditionalPurchaseObligationBalanceOnFifthAnniversary  \
0                                                NaN                    
1                                                NaN                    
2                                                NaN                    

   UnrecordedUnconditionalPurchaseObligationBalanceOnFirstAnniversary  \
0                                                NaN                    
1                                                NaN                    
2                                                NaN                    

   UnrecordedUnconditionalPurchaseObligationBalanceOnFourthAnniversary  \
0                                                NaN                     
1                                                NaN                     
2                                                NaN                     

   UnrecordedUnconditionalPurchaseObligationBalanceOnSecondAnniversary  \
0                                                NaN                     
1                                                NaN                     
2                                                NaN                     

   UnrecordedUnconditionalPurchaseObligationBalanceOnThirdAnniversary  \
0                                                NaN                    
1                                                NaN                    
2                                                NaN                    

   UnrecordedUnconditionalPurchaseObligationDueAfterFiveYears  \
0                                                NaN            
1                                                NaN            
2                                                NaN            

   VariableLeaseCost  WeightedAverageNumberOfDilutedSharesOutstanding  \
0                NaN                                              NaN   
1                NaN                                              NaN   
2                NaN                                              NaN   

   WeightedAverageNumberOfSharesIssuedBasic  \
0                                       NaN   
1                                       NaN   
2                                       NaN   

   WeightedAverageNumberOfSharesOutstandingBasic  
0                                            NaN  
1                                            NaN  
2                                            NaN  

[3 rows x 254 columns]

# Increasing Data Density  
Avoiding low-sampled points to improve signal detection

In [6]:
df.notna().sum().sum(), df.notna().sum().sum() / df.size

(np.int64(18290), np.float64(0.16073186164229472))

In [7]:
# this is an estimate since points are not necessarily sequential
# looking for 2 full periods + 1 full period for validation (1) and test sets (3)
df = df.loc[:,df.notna().sum() >= 12] # need at least two full periods for valid nyquist frequency. 
print(df.shape)
df.notna().sum().sum(), df.notna().sum().sum() / df.size

(448, 226)


(np.int64(18018), np.float64(0.17795907079646017))

In [8]:
from sklearn.preprocessing import MultiLabelBinarizer

binarizer = MultiLabelBinarizer(sparse_output=False)
binarized = binarizer.fit_transform(df["form"].to_numpy().reshape(-1,1))
binarized.shape

(448, 4)

In [9]:
df = pd.concat([df, pd.DataFrame(binarized)], axis=1)
df.shape
df.notna().sum().sum(), df.notna().sum().sum() / df.size

(np.int64(19810), np.float64(0.1922554347826087))

In [10]:
df["period_end"] = df["period_end"].dt.year + df["period_end"].apply(lambda x: x.timetuple().tm_yday) / 366 # leap year
df["filing_date"] = df["filing_date"].dt.year + df["filing_date"].apply(lambda x: x.timetuple().tm_yday) / 366 # leap year
df.head(3)

period_end  filing_date    form  AccountsPayableCurrent  \
0  2006.997268  2010.150273    10-K                     NaN   
1  2007.997268  2009.598361    10-Q                     NaN   
2  2007.997268  2009.846995  10-Q/A                     NaN   

   AccountsReceivableNetCurrent  AccruedAdvertisingCurrent  \
0                           NaN                        NaN   
1                           NaN                        NaN   
2                           NaN                        NaN   

   AccruedLiabilitiesCurrent  AccruedSalariesCurrent  \
0                        NaN                     NaN   
1                        NaN                     NaN   
2                        NaN                     NaN   

   AccumulatedDepreciationDepletionAndAmortizationPropertyPlantAndEquipment  \
0                                                NaN                          
1                                                NaN                          
2                                                NaN                          

   AccumulatedOtherComprehensiveIncomeLossNetOfTax  ...  \
0                                              NaN  ...   
1                                              NaN  ...   
2                                              NaN  ...   

   UnrecordedUnconditionalPurchaseObligationBalanceOnThirdAnniversary  \
0                                                NaN                    
1                                                NaN                    
2                                                NaN                    

   UnrecordedUnconditionalPurchaseObligationDueAfterFiveYears  \
0                                                NaN            
1                                                NaN            
2                                                NaN            

   VariableLeaseCost  WeightedAverageNumberOfDilutedSharesOutstanding  \
0                NaN                                              NaN   
1                NaN                                              NaN   
2                NaN                                              NaN   

   WeightedAverageNumberOfSharesIssuedBasic  \
0                                       NaN   
1                                       NaN   
2                                       NaN   

   WeightedAverageNumberOfSharesOutstandingBasic  0  1  2  3  
0                                            NaN  1  0  0  0  
1                                            NaN  0  1  0  0  
2                                            NaN  0  0  1  0  

[3 rows x 230 columns]

In [11]:
df.to_csv(Path("preprocessed") / "KMB_financials.csv", index=False)